In [1]:
import boto3
import botocore

In [2]:
# Config
REGION = aws_region = boto3.session.Session().region_name # 'us-west-2'

BUCKET = bucket_name = 'andrew-ocr'
document_name = 'jpg-raw/IMG_0102.JPG'

In [3]:
s3 = boto3.client('s3', REGION)

textract = boto3.client('textract', aws_region) 

In [4]:
OUTPUT_PATH = f's3://{BUCKET}/human-review-ocr'

In [5]:
WORKTEAM_ARN= 'arn:aws:sagemaker:us-west-2:652963972038:workteam/private-crowd/ocr-workers'

In [9]:
from sagemaker import get_execution_role

# Setting Role to the default SageMaker Execution Role
ROLE = get_execution_role()
display(ROLE)

Couldn't call 'get_role' to get Role ARN from role name daericks@gmail.com to get Role path.


ValueError: The current AWS identity is not a role: arn:aws:iam::652963972038:user/daericks@gmail.com, therefore it cannot be used as a SageMaker execution role

In [7]:
response = textract.analyze_document(
            Document={'S3Object': {'Bucket': bucket_name, 'Name': document_name}},
            FeatureTypes=["TABLES", "FORMS"],
            HumanLoopConfig={
                'FlowDefinitionArn': 'arn:aws:sagemaker:us-west-2:652963972038:flow-definition/human-review-ocr',
                'HumanLoopName': 'human_loop_first_try',
                'DataAttributes': {'ContentClassifiers': ['FreeOfPersonallyIdentifiableInformation','FreeOfAdultContent']}
            }
          )

InvalidParameterException: An error occurred (InvalidParameterException) when calling the AnalyzeDocument operation: Request has invalid parameters

In [10]:
import boto3
import io
import json
import uuid
import botocore
import time
import botocore

# Amazon SageMaker client
sagemaker = boto3.client('sagemaker', REGION)

# Amazon Textract client
textract = boto3.client('textract', REGION)

# S3 client
s3 = boto3.client('s3', REGION)

# A2I Runtime client
a2i_runtime_client = boto3.client('sagemaker-a2i-runtime', REGION)

In [11]:
import pprint

# Pretty print setup
pp = pprint.PrettyPrinter(indent=2)

# Function to pretty-print AWS SDK responses
def print_response(response):
    if 'ResponseMetadata' in response:
        del response['ResponseMetadata']
    pp.pprint(response)

In [17]:
flowDefinitionArn='arn:aws:sagemaker:us-west-2:652963972038:flow-definition/human-review-ocr'

In [18]:
uniqueId = str(uuid.uuid4())
human_loop_unique_id = uniqueId + '1'

humanLoopConfig = {
    'FlowDefinitionArn':flowDefinitionArn,
    'HumanLoopName':human_loop_unique_id, 
    'DataAttributes': { 'ContentClassifiers': [ 'FreeOfPersonallyIdentifiableInformation' ]}
}

In [20]:
def analyze_document_with_a2i(document_name, bucket):
    response = textract.analyze_document(
        Document={'S3Object': {'Bucket': bucket, 'Name': document_name}},
        FeatureTypes=["TABLES", "FORMS"], 
        HumanLoopConfig=humanLoopConfig
    )
    return response

In [23]:
document= document_name
analyzeDocumentResponse = analyze_document_with_a2i(document, BUCKET)

In [24]:
if 'HumanLoopArn' in analyzeDocumentResponse['HumanLoopActivationOutput']:
    # A human loop has been started!
    print(f'A human loop has been started with ARN: {analyzeDocumentResponse["HumanLoopActivationOutput"]["HumanLoopArn"]}')

A human loop has been started with ARN: arn:aws:sagemaker:us-west-2:652963972038:human-loop/5ec0218b-ed39-439a-8371-2a72ea394a381


In [25]:
all_human_loops_in_workflow = a2i_runtime_client.list_human_loops(FlowDefinitionArn=flowDefinitionArn)['HumanLoopSummaries']

for human_loop in all_human_loops_in_workflow:
    print(f'\nHuman Loop Name: {human_loop["HumanLoopName"]}')
    print(f'Human Loop Status: {human_loop["HumanLoopStatus"]} \n')
    print('\n')


Human Loop Name: 5ec0218b-ed39-439a-8371-2a72ea394a381
Human Loop Status: InProgress 





In [26]:
workteamName = WORKTEAM_ARN[WORKTEAM_ARN.rfind('/') + 1:]
print("Navigate to the private worker portal and do the tasks. Make sure you've invited yourself to your workteam!")
print('https://' + sagemaker.describe_workteam(WorkteamName=workteamName)['Workteam']['SubDomain'])


Navigate to the private worker portal and do the tasks. Make sure you've invited yourself to your workteam!
https://zibdg78f1b.labeling.us-west-2.sagemaker.aws


In [27]:
all_human_loops_in_workflow = a2i_runtime_client.list_human_loops(FlowDefinitionArn=flowDefinitionArn)['HumanLoopSummaries']

completed_loops = []
for human_loop in all_human_loops_in_workflow:
    print(f'\nHuman Loop Name: {human_loop["HumanLoopName"]}')
    print(f'Human Loop Status: {human_loop["HumanLoopStatus"]} \n')
    print('\n')
    if human_loop['HumanLoopStatus'] == 'Completed':
        completed_loops.append(human_loop['HumanLoopName'])


Human Loop Name: 5ec0218b-ed39-439a-8371-2a72ea394a381
Human Loop Status: InProgress 





In [29]:
import re
import pprint
pp = pprint.PrettyPrinter(indent=2)

def retrieve_a2i_results_from_output_s3_uri(bucket, a2i_s3_output_uri):
    '''
    Gets the json file published by A2I and returns a deserialized object
    '''
    splitted_string = re.split('s3://' +  bucket + '/', a2i_s3_output_uri)
    output_bucket_key = splitted_string[1]

    response = s3.get_object(Bucket=bucket, Key=output_bucket_key)
    content = response["Body"].read()
    return json.loads(content)
    

for human_loop_name in completed_loops:

    describe_human_loop_response = a2i_runtime_client.describe_human_loop(
        HumanLoopName=human_loop_name
    )
    
    print(f'\nHuman Loop Name: {describe_human_loop_response["HumanLoopName"]}')
    print(f'Human Loop Status: {describe_human_loop_response["HumanLoopStatus"]}')
    print(f'Human Loop Output Location: : {describe_human_loop_response["HumanLoopOutput"]["OutputS3Uri"]} \n')
    
    # Uncomment below line to print out a2i human answers
    output = retrieve_a2i_results_from_output_s3_uri(BUCKET, describe_human_loop_response['HumanLoopOutput']['OutputS3Uri'])
#     pp.pprint(output)

In [30]:
import webbrowser, os
import json
import boto3
import io
from io import BytesIO
import sys
from pprint import pprint


def get_rows_columns_map(table_result, blocks_map):
    rows = {}
    for relationship in table_result['Relationships']:
        if relationship['Type'] == 'CHILD':
            for child_id in relationship['Ids']:
                cell = blocks_map[child_id]
                if cell['BlockType'] == 'CELL':
                    row_index = cell['RowIndex']
                    col_index = cell['ColumnIndex']
                    if row_index not in rows:
                        # create new row
                        rows[row_index] = {}
                        
                    # get the text value
                    rows[row_index][col_index] = get_text(cell, blocks_map)
    return rows


def get_text(result, blocks_map):
    text = ''
    if 'Relationships' in result:
        for relationship in result['Relationships']:
            if relationship['Type'] == 'CHILD':
                for child_id in relationship['Ids']:
                    word = blocks_map[child_id]
                    if word['BlockType'] == 'WORD':
                        text += word['Text'] + ' '
                    if word['BlockType'] == 'SELECTION_ELEMENT':
                        if word['SelectionStatus'] =='SELECTED':
                            text +=  'X '    
    return text


def get_table_csv_results(file_name):

    with open(file_name, 'rb') as file:
        img_test = file.read()
        bytes_test = bytearray(img_test)
        print('Image loaded', file_name)

    # process using image bytes
    # get the results
    client = boto3.client('textract')

    response = client.analyze_document(Document={'Bytes': bytes_test}, FeatureTypes=['TABLES'])

    # Get the text blocks
    blocks=response['Blocks']
    pprint(blocks)

    blocks_map = {}
    table_blocks = []
    for block in blocks:
        blocks_map[block['Id']] = block
        if block['BlockType'] == "TABLE":
            table_blocks.append(block)

    if len(table_blocks) <= 0:
        return "<b> NO Table FOUND </b>"

    csv = ''
    for index, table in enumerate(table_blocks):
        csv += generate_table_csv(table, blocks_map, index +1)
        csv += '\n\n'

    return csv

def generate_table_csv(table_result, blocks_map, table_index):
    rows = get_rows_columns_map(table_result, blocks_map)

    table_id = 'Table_' + str(table_index)
    
    # get cells.
    csv = 'Table: {0}\n\n'.format(table_id)

    for row_index, cols in rows.items():
        
        for col_index, text in cols.items():
            csv += '{}'.format(text) + ","
        csv += '\n'
        
    csv += '\n\n\n'
    return csv

def main(file_name):
    table_csv = get_table_csv_results(file_name)

    output_file = 'output.csv'

    # replace content
    with open(output_file, "wt") as fout:
        fout.write(table_csv)

    # show the results
    print('CSV OUTPUT FILE: ', output_file)


if __name__ == "__main__":
    file_name = sys.argv[1]
    main(file_name)

FileNotFoundError: [Errno 2] No such file or directory: '-f'

In [31]:
def get_csv(response):
    # Get the text blocks
    blocks=response['Blocks']
    pprint(blocks)

    blocks_map = {}
    table_blocks = []
    for block in blocks:
        blocks_map[block['Id']] = block
        if block['BlockType'] == "TABLE":
            table_blocks.append(block)

    if len(table_blocks) <= 0:
        return "<b> NO Table FOUND </b>"

    csv = ''
    for index, table in enumerate(table_blocks):
        csv += generate_table_csv(table, blocks_map, index +1)
        csv += '\n\n'

    return csv

In [34]:
table_csv = get_csv(analyzeDocumentResponse)

[{'BlockType': 'PAGE',
  'Geometry': {'BoundingBox': {'Height': 0.9640370607376099,
                               'Left': 0.035365909337997437,
                               'Top': 0.025402884930372238,
                               'Width': 0.9238397479057312},
               'Polygon': [{'X': 0.08712485432624817,
                            'Y': 0.025402884930372238},
                           {'X': 0.9392639994621277, 'Y': 0.047021832317113876},
                           {'X': 0.959205687046051, 'Y': 0.9564330577850342},
                           {'X': 0.035365909337997437,
                            'Y': 0.9894399642944336}]},
  'Id': '37e7062d-27d7-4c2c-8801-1facfd7b46f2',
  'Relationships': [{'Ids': ['c080124e-0b9f-4fd1-abf7-e424ca7b15be',
                             '93b97a87-d0fe-4d09-8f59-94c92d09a319',
                             '3729ecc9-c37f-41ce-abb4-66220739dc4d',
                             'e50affba-6f0a-4cc3-8062-04bc589aab15',
                             '

                           {'X': 0.2358238846063614, 'Y': 0.332964152097702}]},
  'Id': 'c24dbdb4-01d8-4b8c-a654-567f2b1153f1',
  'Relationships': [{'Ids': ['e7ec31f1-af9e-4176-be18-f9bc68276592'],
                     'Type': 'CHILD'}],
  'Text': '---'},
 {'BlockType': 'LINE',
  'Confidence': 97.33871459960938,
  'Geometry': {'BoundingBox': {'Height': 0.016832545399665833,
                               'Left': 0.317301481962204,
                               'Top': 0.320131778717041,
                               'Width': 0.03990597277879715},
               'Polygon': [{'X': 0.3178389072418213, 'Y': 0.320131778717041},
                           {'X': 0.3572074770927429, 'Y': 0.32039767503738403},
                           {'X': 0.35672783851623535, 'Y': 0.33696433901786804},
                           {'X': 0.317301481962204, 'Y': 0.33674025535583496}]},
  'Id': 'b3ceceab-e5e5-45fd-9160-961e9cf7723f',
  'Relationships': [{'Ids': ['16690fe3-85a5-408a-aca2-347a39bf69e1'],
        

                               'Width': 0.0719766840338707},
               'Polygon': [{'X': 0.3020953834056854, 'Y': 0.4884309470653534},
                           {'X': 0.3734308183193207, 'Y': 0.4881393611431122},
                           {'X': 0.3729093372821808, 'Y': 0.507343590259552},
                           {'X': 0.3014541268348694, 'Y': 0.507724404335022}]},
  'Id': '98b61143-4224-47f4-a248-42a17d132ce7',
  'Relationships': [{'Ids': ['d7afff92-1bd3-4f92-bc6e-b6b87b67db44',
                             'b9f5e795-8eaf-430c-82df-b0b1d80f1525'],
                     'Type': 'CHILD'}],
  'Text': "City's 2/3"},
 {'BlockType': 'LINE',
  'Confidence': 99.54641723632812,
  'Geometry': {'BoundingBox': {'Height': 0.01905064843595028,
                               'Left': 0.3972044587135315,
                               'Top': 0.4875005781650543,
                               'Width': 0.06997209787368774},
               'Polygon': [{'X': 0.3976753056049347, 'Y': 0.487783491611

                               'Width': 0.19703079760074615},
               'Polygon': [{'X': 0.7028900384902954, 'Y': 0.6252723932266235},
                           {'X': 0.8995585441589355, 'Y': 0.6226687431335449},
                           {'X': 0.8999208807945251, 'Y': 0.6433535218238831},
                           {'X': 0.7029095888137817, 'Y': 0.6462345719337463}]},
  'Id': '64851928-f8f9-41f8-a8d2-081870250c80',
  'Relationships': [{'Ids': ['ba182843-8002-4275-a7e2-7451d6327b43',
                             '55ed9d3c-4604-4eef-8639-5b0450ce948d',
                             '6a1450c3-c047-4676-b2a1-d7195dfc1b96',
                             '23659d0c-d3c5-47cc-ba2e-46363e0a7bf0',
                             'fdeec1a8-1964-4a48-84e2-12b5e8138315'],
                     'Type': 'CHILD'}],
  'Text': '$6,500; Planning Engineer - $6,000.'},
 {'BlockType': 'LINE',
  'Confidence': 13.388219833374023,
  'Geometry': {'BoundingBox': {'Height': 0.017412738874554634,
              

                               'Width': 0.03399805724620819},
               'Polygon': [{'X': 0.48165300488471985, 'Y': 0.7648686766624451},
                           {'X': 0.5155116319656372, 'Y': 0.764119029045105},
                           {'X': 0.5153949856758118, 'Y': 0.7720626592636108},
                           {'X': 0.4815135896205902, 'Y': 0.7728303670883179}]},
  'Id': '470e1ecf-1e44-4c63-ba33-0381ba68e5c3',
  'Relationships': [{'Ids': ['340a146e-5017-4997-9725-026f90ae5b17'],
                     'Type': 'CHILD'}],
  'Text': '---'},
 {'BlockType': 'LINE',
  'Confidence': 37.16981887817383,
  'Geometry': {'BoundingBox': {'Height': 0.006700159516185522,
                               'Left': 0.5948331356048584,
                               'Top': 0.7624481320381165,
                               'Width': 0.03213481232523918},
               'Polygon': [{'X': 0.594881534576416, 'Y': 0.763160228729248},
                           {'X': 0.6269679665565491, 'Y': 0.7624481

...

                            'Y': 0.4488447308540344}]},
  'Id': 'cfe2c078-9526-4503-82d5-aa4c32b376b7',
  'Relationships': [{'Ids': ['0074e1e2-3f4a-4816-bba2-5386d122fc8a'],
                     'Type': 'CHILD'}],
  'RowIndex': 4,
  'RowSpan': 1},
 {'BlockType': 'CELL',
  'ColumnIndex': 6,
  'ColumnSpan': 1,
  'Confidence': 81.12728881835938,
  'Geometry': {'BoundingBox': {'Height': 0.14556725323200226,
                               'Left': 0.5699013471603394,
                               'Top': 0.3031274676322937,
                               'Width': 0.11016041785478592},
               'Polygon': [{'X': 0.5714200139045715, 'Y': 0.3031274676322937},
                           {'X': 0.6800617575645447, 'Y': 0.30399447679519653},
                           {'X': 0.6799145340919495, 'Y': 0.44852352142333984},
                           {'X': 0.5699013471603394,
                            'Y': 0.44869473576545715}]},
  'Id': 'ef69d13f-cdcc-4f51-b4a7-8703f5e4fabc',
  'Relationships'

  'Geometry': {'BoundingBox': {'Height': 0.04647768288850784,
                               'Left': 0.09631495177745819,
                               'Top': 0.5845347046852112,
                               'Width': 0.10454439371824265},
               'Polygon': [{'X': 0.09859462827444077, 'Y': 0.5855786204338074},
                           {'X': 0.20085935294628143, 'Y': 0.5845347046852112},
                           {'X': 0.19898496568202972, 'Y': 0.629668116569519},
                           {'X': 0.09631495177745819,
                            'Y': 0.6310123801231384}]},
  'Id': '371cedaa-3481-410c-8f58-3e92b2cee871',
  'Relationships': [{'Ids': ['25eff1d8-1ba8-41c9-97af-07338f645cd7'],
                     'Type': 'CHILD'}],
  'RowIndex': 7,
  'RowSpan': 1},
 {'BlockType': 'CELL',
  'ColumnIndex': 2,
  'ColumnSpan': 1,
  'Confidence': 93.99156188964844,
  'Geometry': {'BoundingBox': {'Height': 0.0459829680621624,
                               'Left': 0.19898496568202972,

                           {'X': 0.19402723014354706, 'Y': 0.7490460276603699},
                           {'X': 0.09028466045856476,
                            'Y': 0.7511956691741943}]},
  'Id': '4f09de6c-b06b-41f3-9911-7145468dd5d7',
  'Relationships': [{'Ids': ['f12547a0-e723-4904-9e3c-d8a4bcb70fd6'],
                     'Type': 'CHILD'}],
  'RowIndex': 9,
  'RowSpan': 1},
 {'BlockType': 'CELL',
  'ColumnIndex': 2,
  'ColumnSpan': 1,
  'Confidence': 89.65789794921875,
  'Geometry': {'BoundingBox': {'Height': 0.08313155919313431,
                               'Left': 0.19402723014354706,
                               'Top': 0.6659144759178162,
                               'Width': 0.0872211828827858},
               'Polygon': [{'X': 0.1974257379770279, 'Y': 0.6672130823135376},
                           {'X': 0.28124842047691345, 'Y': 0.6659144759178162},
                           {'X': 0.27844133973121643, 'Y': 0.7472968697547913},
                           {'X': 0.194027

  'Geometry': {'BoundingBox': {'Height': 0.06431261450052261,
                               'Left': 0.46599942445755005,
                               'Top': 0.7865821719169617,
                               'Width': 0.10037682950496674},
               'Polygon': [{'X': 0.46715694665908813, 'Y': 0.788932204246521},
                           {'X': 0.566376268863678, 'Y': 0.7865821719169617},
                           {'X': 0.5657341480255127, 'Y': 0.8481307029724121},
                           {'X': 0.46599942445755005,
                            'Y': 0.8508948087692261}]},
  'Id': '46e54715-7ccd-4dec-9857-a4d85c5e7548',
  'Relationships': [{'Ids': ['40ac49b9-b321-4a29-8f6c-1f17a4a4c9c8'],
                     'Type': 'CHILD'}],
  'RowIndex': 11,
  'RowSpan': 1},
 {'BlockType': 'CELL',
  'ColumnIndex': 6,
  'ColumnSpan': 1,
  'Confidence': 75.11051177978516,
  'Geometry': {'BoundingBox': {'Height': 0.06422954797744751,
                               'Left': 0.5657341480255127,
 

                     'Type': 'CHILD'}]},
 {'BlockType': 'KEY_VALUE_SET',
  'Confidence': 22.0,
  'EntityTypes': ['KEY'],
  'Geometry': {'BoundingBox': {'Height': 0.022960208356380463,
                               'Left': 0.747612476348877,
                               'Top': 0.22646668553352356,
                               'Width': 0.041656848043203354},
               'Polygon': [{'X': 0.747612476348877, 'Y': 0.22646668553352356},
                           {'X': 0.7890791893005371, 'Y': 0.22701217234134674},
                           {'X': 0.7892693281173706, 'Y': 0.24942690134048462},
                           {'X': 0.7477219104766846,
                            'Y': 0.24894225597381592}]},
  'Id': '7dcb16bf-3dd6-4075-bed5-b5321321aa1e',
  'Relationships': [{'Ids': ['cda3d698-d10a-443f-9e18-a5ba30fe91f7'],
                     'Type': 'VALUE'}]},
 {'BlockType': 'KEY_VALUE_SET',
  'Confidence': 22.0,
  'EntityTypes': ['VALUE'],
  'Geometry': {'BoundingBox': {'Height': 0.018

In [36]:
output_file = 'output.csv'

# replace content
with open(output_file, "wt") as fout:
    fout.write(table_csv)

# show the results
print('CSV OUTPUT FILE: ', output_file)

CSV OUTPUT FILE:  output.csv


In [47]:
def analyze_pdf_document_with_a2i(document_name, bucket):
    response = textract.start_document_analysis(
        DocumentLocation={'S3Object': {'Bucket': bucket, 'Name': document_name}},
        FeatureTypes=["TABLES", "FORMS"], 
#         HumanLoopConfig=humanLoopConfig
    )
    return response

In [52]:
doc= 'jpg-raw/part1-thru0309.pdf'
analyzePDF = analyze_pdf_document_with_a2i(doc, BUCKET)

In [56]:
table_csv = get_csv(analyzePDF)
output_file = 'output-part1.csv'

# replace content
with open(output_file, "wt") as fout:
    fout.write(table_csv)

# show the results
print('CSV OUTPUT FILE: ', output_file)

KeyError: 'Blocks'

In [55]:
analyzePDF

{'JobId': 'e65b673f999d48fdbfbb064a2b3ea62d9e9c57012997686442b9ea7231c914fa',
 'ResponseMetadata': {'RequestId': '8f9b4731-9939-44b1-ac4c-9f8df69caae8',
  'HTTPStatusCode': 200,
  'HTTPHeaders': {'x-amzn-requestid': '8f9b4731-9939-44b1-ac4c-9f8df69caae8',
   'content-type': 'application/x-amz-json-1.1',
   'content-length': '76',
   'date': 'Thu, 09 Sep 2021 23:39:54 GMT'},
  'RetryAttempts': 0}}

In [57]:
analyzePDF['JobId']

'e65b673f999d48fdbfbb064a2b3ea62d9e9c57012997686442b9ea7231c914fa'

In [58]:
analyzePDF_results= textract.get_document_analysis(
    JobId=analyzePDF['JobId']
)

In [59]:
analyzePDF_results

{'DocumentMetadata': {'Pages': 241},
 'JobStatus': 'SUCCEEDED',
 'NextToken': 'mZEttZNZj0yBDvf+PqnVRkH7IbjaezVAZMfzAZQtU1GhViF/r05C7Rub2RKYi1B49xM7C52FCzWv0BMo0sJYerpAkSpMFaPvXsllJ/Xdyi55HfZ1ng==',
 'Blocks': [{'BlockType': 'PAGE',
   'Geometry': {'BoundingBox': {'Width': 0.988946795463562,
     'Height': 0.976067066192627,
     'Left': 0.005862809717655182,
     'Top': 0.005486753303557634},
    'Polygon': [{'X': 0.005862809717655182, 'Y': 0.9114241003990173},
     {'X': 0.01933825947344303, 'Y': 0.02792367897927761},
     {'X': 0.9848500490188599, 'Y': 0.005486753303557634},
     {'X': 0.994809627532959, 'Y': 0.9815537929534912}]},
   'Id': 'e58e7036-87a4-4d67-b20e-f75890b507cc',
   'Relationships': [{'Type': 'CHILD',
     'Ids': ['8db5b508-4482-49fd-96de-32fbbe36a816',
      '348db637-ab12-4a38-a98f-02c10cdf35e0',
      '4bbb078a-94c6-4c46-95f0-613411a76ab3',
      '0e23d71e-6d51-4025-b703-3a43c67d34c5',
      '6ea0357f-7eb3-49c1-a6f2-9fca0219f529',
      'f9525d88-71d1-403a-a240-9e

In [61]:
import json
with open('pdf-results-part1.txt', 'w') as file:
    file.write(json.dumps(analyzePDF_results)) # use 'json.loads' to do the reverse

In [62]:
analyzePDF_results

{'DocumentMetadata': {'Pages': 241},
 'JobStatus': 'SUCCEEDED',
 'NextToken': 'mZEttZNZj0yBDvf+PqnVRkH7IbjaezVAZMfzAZQtU1GhViF/r05C7Rub2RKYi1B49xM7C52FCzWv0BMo0sJYerpAkSpMFaPvXsllJ/Xdyi55HfZ1ng==',
 'Blocks': [{'BlockType': 'PAGE',
   'Geometry': {'BoundingBox': {'Width': 0.988946795463562,
     'Height': 0.976067066192627,
     'Left': 0.005862809717655182,
     'Top': 0.005486753303557634},
    'Polygon': [{'X': 0.005862809717655182, 'Y': 0.9114241003990173},
     {'X': 0.01933825947344303, 'Y': 0.02792367897927761},
     {'X': 0.9848500490188599, 'Y': 0.005486753303557634},
     {'X': 0.994809627532959, 'Y': 0.9815537929534912}]},
   'Id': 'e58e7036-87a4-4d67-b20e-f75890b507cc',
   'Relationships': [{'Type': 'CHILD',
     'Ids': ['8db5b508-4482-49fd-96de-32fbbe36a816',
      '348db637-ab12-4a38-a98f-02c10cdf35e0',
      '4bbb078a-94c6-4c46-95f0-613411a76ab3',
      '0e23d71e-6d51-4025-b703-3a43c67d34c5',
      '6ea0357f-7eb3-49c1-a6f2-9fca0219f529',
      'f9525d88-71d1-403a-a240-9e

In [64]:
results_csv = get_csv(analyzePDF_results)

[{'BlockType': 'PAGE',
  'Geometry': {'BoundingBox': {'Height': 0.976067066192627,
                               'Left': 0.005862809717655182,
                               'Top': 0.005486753303557634,
                               'Width': 0.988946795463562},
               'Polygon': [{'X': 0.005862809717655182, 'Y': 0.9114241003990173},
                           {'X': 0.01933825947344303, 'Y': 0.02792367897927761},
                           {'X': 0.9848500490188599, 'Y': 0.005486753303557634},
                           {'X': 0.994809627532959, 'Y': 0.9815537929534912}]},
  'Id': 'e58e7036-87a4-4d67-b20e-f75890b507cc',
  'Page': 1,
  'Relationships': [{'Ids': ['8db5b508-4482-49fd-96de-32fbbe36a816',
                             '348db637-ab12-4a38-a98f-02c10cdf35e0',
                             '4bbb078a-94c6-4c46-95f0-613411a76ab3',
                             '0e23d71e-6d51-4025-b703-3a43c67d34c5',
                             '6ea0357f-7eb3-49c1-a6f2-9fca0219f529',
       

                               'Top': 0.26335278153419495,
                               'Width': 0.0038087849970906973},
               'Polygon': [{'X': 0.2778306007385254, 'Y': 0.2680690884590149},
                           {'X': 0.27787014842033386, 'Y': 0.26335278153419495},
                           {'X': 0.2816393971443176, 'Y': 0.2633594572544098},
                           {'X': 0.28160029649734497,
                            'Y': 0.2680776119232178}]},
  'Id': '88cad1e6-932c-4a6f-9d85-daacf151c940',
  'Page': 1,
  'Relationships': [{'Ids': ['09276d29-247f-4f9b-8baf-879a15390ccc'],
                     'Type': 'CHILD'}],
  'Text': '-'},
 {'BlockType': 'LINE',
  'Confidence': 42.684959411621094,
  'Geometry': {'BoundingBox': {'Height': 0.038145728409290314,
                               'Left': 0.27629464864730835,
                               'Top': 0.6490609645843506,
                               'Width': 0.015277405269443989},
               'Polygon': [{'X': 0.276

 {'BlockType': 'LINE',
  'Confidence': 55.202667236328125,
  'Geometry': {'BoundingBox': {'Height': 0.03954208269715309,
                               'Left': 0.35656484961509705,
                               'Top': 0.6486471891403198,
                               'Width': 0.016680080443620682},
               'Polygon': [{'X': 0.35656484961509705, 'Y': 0.6874432563781738},
                           {'X': 0.35680750012397766, 'Y': 0.6486471891403198},
                           {'X': 0.37324491143226624, 'Y': 0.6493269205093384},
                           {'X': 0.37301841378211975,
                            'Y': 0.6881892681121826}]},
  'Id': 'f81d6b98-7a37-442f-a76f-f2a650e3ed41',
  'Page': 1,
  'Relationships': [{'Ids': ['f6df8d1e-df69-4ed5-9d0d-0b5036959b76'],
                     'Type': 'CHILD'}],
  'Text': '7.000'},
 {'BlockType': 'LINE',
  'Confidence': 15.349268913269043,
  'Geometry': {'BoundingBox': {'Height': 0.03685763105750084,
                               'Left

                             '77b2404f-b751-4821-a389-4855298e6d55'],
                     'Type': 'CHILD'}],
  'Text': 'Supt. Water 1'},
 {'BlockType': 'LINE',
  'Confidence': 71.48367309570312,
  'Geometry': {'BoundingBox': {'Height': 0.04271380230784416,
                               'Left': 0.5354583859443665,
                               'Top': 0.9003759622573853,
                               'Width': 0.015150331892073154},
               'Polygon': [{'X': 0.5354583859443665, 'Y': 0.942029595375061},
                           {'X': 0.535525381565094, 'Y': 0.9003759622573853},
                           {'X': 0.5506086945533752, 'Y': 0.9013715386390686},
                           {'X': 0.5505577921867371, 'Y': 0.9430897235870361}]},
  'Id': '89313d1c-777b-4cdb-83da-6480eb6c0d8d',
  'Page': 1,
  'Relationships': [{'Ids': ['b02b0c00-90c2-4912-a3bf-993159d837d8',
                             '4f9c223a-b9a2-4e1a-a03c-5c77c9189d49'],
                     'Type': 'CHILD'}],
  'Tex

  'Relationships': [{'Ids': ['ef0ffab5-48fb-4d19-9ec8-db9c1496bcf7',
                             'e4d029a4-ff64-4eba-91f4-96606b92ee6a',
                             'f63fbe3d-c4a3-4ac4-aa31-9bd684c4b811',
                             'f4146ab5-049a-4af9-b4ae-5752647d3fdd'],
                     'Type': 'CHILD'}],
  'Text': '& Clerk of Council-'},
 {'BlockType': 'LINE',
  'Confidence': 70.43275451660156,
  'Geometry': {'BoundingBox': {'Height': 0.1975463330745697,
                               'Left': 0.6189126372337341,
                               'Top': 0.09978140890598297,
                               'Width': 0.02331325225532055},
               'Polygon': [{'X': 0.6190211772918701, 'Y': 0.29720935225486755},
                           {'X': 0.6189126372337341, 'Y': 0.10011890530586243},
                           {'X': 0.6419970989227295, 'Y': 0.09978140890598297},
                           {'X': 0.6422258615493774,
                            'Y': 0.29732775688171387}]},


...

  'Id': '680aad97-8c7a-4595-bd63-6b787870af98',
  'Page': 3,
  'Relationships': [{'Ids': ['0923ba77-77c4-42a4-8b29-4ff1118d2de7'],
                     'Type': 'CHILD'}],
  'RowIndex': 9,
  'RowSpan': 1},
 {'BlockType': 'CELL',
  'ColumnIndex': 8,
  'ColumnSpan': 1,
  'Confidence': 75.3257064819336,
  'Geometry': {'BoundingBox': {'Height': 0.10063479095697403,
                               'Left': 0.32594674825668335,
                               'Top': 0.6043897271156311,
                               'Width': 0.02699829451739788},
               'Polygon': [{'X': 0.35220202803611755, 'Y': 0.6043897271156311},
                           {'X': 0.3529450297355652, 'Y': 0.7048623561859131},
                           {'X': 0.3269267976284027, 'Y': 0.7050245404243469},
                           {'X': 0.32594674825668335,
                            'Y': 0.6045090556144714}]},
  'Id': '65a3330a-5a26-428f-8a45-aa6317526d2f',
  'Page': 3,
  'Relationships': [{'Ids': ['e1331fd6-ecbe-4ccf

  'Relationships': [{'Ids': ['26407914-284a-43dc-b91a-0bed46773762'],
                     'Type': 'CHILD'}],
  'RowIndex': 12,
  'RowSpan': 1},
 {'BlockType': 'CELL',
  'ColumnIndex': 5,
  'ColumnSpan': 1,
  'Confidence': 91.05438995361328,
  'Geometry': {'BoundingBox': {'Height': 0.07594912499189377,
                               'Left': 0.1411776840686798,
                               'Top': 0.31782445311546326,
                               'Width': 0.05396381765604019},
               'Polygon': [{'X': 0.1935414969921112, 'Y': 0.3178386688232422},
                           {'X': 0.1951414942741394, 'Y': 0.3937215209007263},
                           {'X': 0.14312687516212463, 'Y': 0.3937735855579376},
                           {'X': 0.1411776840686798,
                            'Y': 0.31782445311546326}]},
  'Id': 'dc4fa9a9-a2e3-4ced-9a5a-93fdbcbd055f',
  'Page': 3,
  'Relationships': [{'Ids': ['a10eb30c-bfb4-4842-8db9-597ee2f37091'],
                     'Type': 'CHILD'}

                            'Y': 0.10088729858398438}]},
  'Id': 'f5acbb3f-daab-4770-864e-38e974663294',
  'Page': 3,
  'Relationships': [{'Ids': ['82fde7db-6277-43e6-8a72-076c4461d69d'],
                     'Type': 'VALUE'},
                    {'Ids': ['26d20533-35b5-4fb4-868c-dd133cbeb7df',
                             '26776216-6af1-4ce5-bda6-0fc143250c2a',
                             '4092118f-bde4-49de-ba14-77a5abaddb31'],
                     'Type': 'CHILD'}]},
 {'BlockType': 'KEY_VALUE_SET',
  'Confidence': 25.5,
  'EntityTypes': ['VALUE'],
  'Geometry': {'BoundingBox': {'Height': 0.06110827252268791,
                               'Left': 0.7939905524253845,
                               'Top': 0.1008758693933487,
                               'Width': 0.030720386654138565},
               'Polygon': [{'X': 0.8247109055519104, 'Y': 0.1009896844625473},
                           {'X': 0.8226689100265503, 'Y': 0.1619841456413269},
                           {'X': 0.7939905

                     'Type': 'VALUE'},
                    {'Ids': ['40f6174a-f552-4948-ac2f-88a58fb46933',
                             'c34aff66-4059-435e-a86a-327a1e945165'],
                     'Type': 'CHILD'}]},
 {'BlockType': 'KEY_VALUE_SET',
  'Confidence': 13.500000953674316,
  'EntityTypes': ['VALUE'],
  'Geometry': {'BoundingBox': {'Height': 0.04278085008263588,
                               'Left': 0.5514640212059021,
                               'Top': 0.8057094812393188,
                               'Width': 0.01692214049398899},
               'Polygon': [{'X': 0.5683861970901489, 'Y': 0.8057094812393188},
                           {'X': 0.567865252494812, 'Y': 0.8483480215072632},
                           {'X': 0.5514640212059021, 'Y': 0.848490297794342},
                           {'X': 0.5519209504127502, 'Y': 0.8058404922485352}]},
  'Id': '9f98e870-d441-4214-ba6d-bb7d2e2861b6',
  'Page': 3},
 {'BlockType': 'PAGE',
  'Geometry': {'BoundingBox': {'Height': 0.

                           {'X': 0.1412220150232315, 'Y': 0.9209259748458862}]},
  'Id': '5cdf1b1d-82a9-4e6c-9c6f-b53e6c6b157f',
  'Page': 4,
  'Relationships': [{'Ids': ['82fff327-f48b-4431-bb74-e33c7de1a676'],
                     'Type': 'CHILD'}],
  'Text': 'Municipality'},
 {'BlockType': 'LINE',
  'Confidence': 99.75315856933594,
  'Geometry': {'BoundingBox': {'Height': 0.04436861351132393,
                               'Left': 0.1161215677857399,
                               'Top': 0.74027019739151,
                               'Width': 0.01605140045285225},
               'Polygon': [{'X': 0.11842702329158783, 'Y': 0.7844703197479248},
                           {'X': 0.1161215677857399, 'Y': 0.74027019739151},
                           {'X': 0.12989473342895508, 'Y': 0.7404105067253113},
                           {'X': 0.13217297196388245,
                            'Y': 0.7846388220787048}]},
  'Id': '6ee9411f-b668-4630-bcaa-d140d7ccb9c6',
  'Page': 4,
  'Relationships

In [67]:
output_file = 'output-part1.csv'

# replace content
with open(output_file, "wt") as fout:
    fout.write(results_csv)

# show the results
print('CSV OUTPUT FILE: ', output_file)

CSV OUTPUT FILE:  output-part1.csv


In [68]:
results_csv

"Table: Table_1\n\nComptroller ,Auditor ,Treasurer ,Comm. of Revenue ,Director of Public Welfare ,Director of Public Health ,Director of Public ,Dinctor of ,,\nsignity $ None dris ,$ None ,$ 8,650 3.000 ,$ 8,800 3,000 ,$ 5,400 ,$11,287.50 Neme ,Works $10,750 - ,$1400 -$7, ,Real ,\nagtion ,--- ,9,000 7.000 ,9,000 ,6,930 ,9,750 7.300 ,10,600 Director- $8,450 ments-$7,400; - Director of Public ,1450 Drector Dinctor of Inspections - Safety-$9.40. ,Finance Director. Real Estate Assess- $8,450; Personne) Libraries-$7,50 $8,450; Director t6 ,\n- - ,Clerk ,3,600 City's 2/3 ,3,814 City's 2/3 ,4,410 ,--- Public Wellare ,4,500 ,,,\nluma Vista ... ,--- ,3,432 ,3,000 ,3,000 ,- - ,3,060 Supt. ,,Supt. Water 1 Sewer-$3,060, ,\n... ,--- ,6,800 ,5,500 ,4,500 ,9,500 ,... ,4,120 ,Director of Finance & Clerk of Council- ,\n,,9.900 ,9,900 ,10,408 ,,$6,500; ,Plannisg.bgineer-$6,000. ,- ,\n13.440 Parille --- ,9.360 --- ,2,533 City's 1/3 ,5,850 City's 2/3 ,4,800 ,9,000 ,8,200 ,1,00 ,Director of Finance & Clerk

In [73]:
analyzePDF_results.keys()

dict_keys(['DocumentMetadata', 'JobStatus', 'NextToken', 'Blocks', 'AnalyzeDocumentModelVersion', 'ResponseMetadata'])

In [78]:
analyzePDF_results["NextToken"]

'mZEttZNZj0yBDvf+PqnVRkH7IbjaezVAZMfzAZQtU1GhViF/r05C7Rub2RKYi1B49xM7C52FCzWv0BMo0sJYerpAkSpMFaPvXsllJ/Xdyi55HfZ1ng=='

In [77]:
cnt=0
for block in analyzePDF_results['Blocks']:
    if block['BlockType']=="TABLE":
        cnt += 1
        print(cnt)

1
2


In [79]:
analyzePDF.keys()

dict_keys(['JobId', 'ResponseMetadata'])

In [83]:
def GetResults(jobId):
    maxResults = 1000
    paginationToken = None
    finished = False
    while finished == False:
        response = None
#         if self.processType == ProcessType.ANALYSIS:
        if paginationToken == None:
#             response = self.textract.get_document_analysis(JobId=jobId, MaxResults=maxResults)
            response = textract.get_document_analysis(JobId=analyzePDF['JobId'])
        else:
#             response = self.textract.get_document_analysis(JobId=jobId, MaxResults=maxResults, NextToken=paginationToken)
            response = textract.get_document_analysis(JobId=analyzePDF['JobId'], NextToken=paginationToken)
#         if self.processType == ProcessType.DETECTION:
#            if paginationToken == None:
#                response = self.textract.get_document_text_detection(JobId=jobId, MaxResults=maxResults)
#            else:
#                response = self.textract.get_document_text_detection(JobId=jobId,MaxResults=maxResults, NextToken=paginationToken)
        blocks = response['Blocks']
        print('Detected Document Text')
        print('Pages: {}'.format(response['DocumentMetadata']['Pages']))
        # Display block information
#         for block in blocks:
#            self.DisplayBlockInfo(block)
#            print()
#            print()
        if 'NextToken' in response:
           paginationToken = response['NextToken']
        else:
            finished = True
            return response


In [86]:
analyzePDF_results.keys()

dict_keys(['DocumentMetadata', 'JobStatus', 'NextToken', 'Blocks', 'AnalyzeDocumentModelVersion', 'ResponseMetadata'])

In [87]:
analyzePDF_results['Blocks']

[{'BlockType': 'PAGE',
  'Geometry': {'BoundingBox': {'Width': 0.988946795463562,
    'Height': 0.976067066192627,
    'Left': 0.005862809717655182,
    'Top': 0.005486753303557634},
   'Polygon': [{'X': 0.005862809717655182, 'Y': 0.9114241003990173},
    {'X': 0.01933825947344303, 'Y': 0.02792367897927761},
    {'X': 0.9848500490188599, 'Y': 0.005486753303557634},
    {'X': 0.994809627532959, 'Y': 0.9815537929534912}]},
  'Id': 'e58e7036-87a4-4d67-b20e-f75890b507cc',
  'Relationships': [{'Type': 'CHILD',
    'Ids': ['8db5b508-4482-49fd-96de-32fbbe36a816',
     '348db637-ab12-4a38-a98f-02c10cdf35e0',
     '4bbb078a-94c6-4c46-95f0-613411a76ab3',
     '0e23d71e-6d51-4025-b703-3a43c67d34c5',
     '6ea0357f-7eb3-49c1-a6f2-9fca0219f529',
     'f9525d88-71d1-403a-a240-9e97951b41a6',
     '9606cc0d-3245-4bba-8f2e-2673f296adbb',
     '3fa91a11-d810-442f-9ca7-ae3b3c905baa',
     '33d31560-b5af-4147-9963-08ecb73ee89f',
     '21efb64f-063b-4ff7-bdda-7643b0da1276',
     '4f6efa44-bc22-46ce-9475-2f

In [91]:
analyzePDF_results = textract.get_document_analysis(JobId=analyzePDF['JobId'])
paginationToken= analyzePDF_results['NextToken']
analyzePDF_results2 = textract.get_document_analysis(JobId=analyzePDF['JobId'], NextToken=paginationToken)

In [96]:
analyzePDF_results2.keys()

dict_keys(['DocumentMetadata', 'JobStatus', 'NextToken', 'Blocks', 'AnalyzeDocumentModelVersion', 'ResponseMetadata'])

In [97]:
analyzePDF_results2['ResponseMetadata']

{'RequestId': '000945fe-4454-49ee-809a-61289c1e4ec7',
 'HTTPStatusCode': 200,
 'HTTPHeaders': {'x-amzn-requestid': '000945fe-4454-49ee-809a-61289c1e4ec7',
  'content-type': 'application/x-amz-json-1.1',
  'content-length': '543151',
  'date': 'Mon, 13 Sep 2021 17:21:30 GMT'},
 'RetryAttempts': 0}

In [95]:
print(analyzePDF_results['DocumentMetadata'], 
      analyzePDF_results2['DocumentMetadata'])

{'Pages': 241} {'Pages': 241}


In [92]:
analyzePDF_results2

{'DocumentMetadata': {'Pages': 241},
 'JobStatus': 'SUCCEEDED',
 'NextToken': 'mZEttZNZj0yBDvf+PqnVRkH7IbjaezVAZMfzAZQtU1GhViF/r05C7Rub2RKYi1B49xM7C52FCzWv0BMo0sJYerpAkSpMFaPoXs1jLfDVzSx5HvZ1ng==',
 'Blocks': [{'BlockType': 'LINE',
   'Confidence': 71.55050659179688,
   'Text': '---',
   'Geometry': {'BoundingBox': {'Width': 0.0057271323166787624,
     'Height': 0.022356553003191948,
     'Left': 0.21548856794834137,
     'Top': 0.7664579153060913},
    'Polygon': [{'X': 0.21654854714870453, 'Y': 0.7887566089630127},
     {'X': 0.21548856794834137, 'Y': 0.7664579153060913},
     {'X': 0.22016039490699768, 'Y': 0.7665110230445862},
     {'X': 0.22121569514274597, 'Y': 0.7888144850730896}]},
   'Id': '541e543a-1c5c-4ab1-a2a8-1cd86be4a66d',
   'Relationships': [{'Type': 'CHILD',
     'Ids': ['1bb4e0be-7a46-46de-b7d8-c1b70cd99cf0']}],
   'Page': 4},
  {'BlockType': 'LINE',
   'Confidence': 87.39837646484375,
   'Text': '---',
   'Geometry': {'BoundingBox': {'Width': 0.0057321228086948395,
